# Lagrangian particle tracking

Material particles following ocean currents can be analyzed in terms of trajectories. These can simply be computed by integrating velocities through time within a [Lagrangian framework](https://en.wikipedia.org/wiki/Lagrangian_and_Eulerian_specification_of_the_flow_field). In `Julia` this is easily done using the [IndividualDisplacements.jl](https://JuliaClimate.github.io/IndividualDisplacements.jl/dev/) and [OrdinaryDiffEq.jl](https://docs.juliadiffeq.org/latest) packages.

## Import software, grid, and velocity fields

1. pre-requisites
2. read variables

In [1]:
#]add MITgcmTools#master; add OrdinaryDiffEq; add IndividualDisplacements#master;

In [2]:
using IndividualDisplacements, MeshArrays, OrdinaryDiffEq
using Plots, Statistics, MITgcmTools, DataFrames

include("helper_functions.jl")
get_grid_if_needed()
get_velocity_if_needed()

γ=read_llc90_grid();

## Set Gridded Variables

1. Select depth
2. time average & normalize to grid units
3. apply exchange function to `u,v,lon,lat`
4. store everything in `uv_etc` dictionary

In [3]:
uv_etc=read_uv_etc(20,γ);

## Initialize Trajectory Computation

1. set `duComp` to interpolation function
2. set `u0` initial location array

In [4]:
du_dt=IndividualDisplacements.VelComp!
(u0,du)=initialize_locations(uv_etc,10);

## Compute Trajectories

_Note: `ODEProblem` and `solve` settings can still be refined_

In [5]:
tspan = (0.0,uv_etc["t1"]-uv_etc["t0"])
prob = ODEProblem(du_dt,u0,tspan,uv_etc)
sol = solve(prob,Euler(),dt=uv_etc["dt"])
size(sol)

(3, 5441, 367)

## Post-Process Trajectories

1. Copy `sol` to a `DataFrame`
2. Map position to lon,lat coordinates

In [6]:
df=postprocess_ODESolution(sol,uv_etc);

## Plot Trajectories


For example, you can:

- use either `Makie.jl` via `PlotMakie`
- or use `PyPlot.jl` via `PlotMapProj`


In [7]:
p=dirname(pathof(IndividualDisplacements));

In [8]:
#include(joinpath(p,"plot_pyplot.jl")); 
#PyPlot.figure(); PlotMapProj(df,5000)

#include(joinpath(p,"plot_makie.jl")); AbstractPlotting.inline!(true); #for Juno, set to false
#scene=PlotMakie(df,5000,180.0) #Makie.save("LatLonCap300mDepth.png", scene)

include(joinpath(p,"plot_plots.jl")); 
plt=PlotBasic(df,1000,180.0)